# IBM Data Science Professional Certificate - Final Project

## Scrapping the data from wikipedia 

In [158]:
import requests  
import pandas as pd
import matplotlib.pyplot as plt

In [159]:
# url of wikipedia page from which you want to scrap tabular data.
url1 = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"

# determine the index of your table
df = pd.read_html(url1, header = 0)[0]

# Igonre cells with not assigned borough 
df = df[df.Borough != 'Not assigned']

In [160]:
df = df.groupby(['Postal Code', 'Borough'])['Neighbourhood'].apply(list).apply(lambda x:', '.join(x)).to_frame().reset_index()
df.describe()



Postal Code     Borough Neighbourhood
count          103         103           103
unique         103          10            99
top            M9W  North York     Downsview
freq             1          24             4

### Cleaning Data 

In [161]:
for index, row in df.iterrows():
    if row['Neighbourhood'] == 'Not assigned':
        row['Neighbourhood'] == row['Borough']

In [162]:
# define the dataframe columns
column_names = ['Postal Code','Borough', 'Neighbourhood'] 

# instantiate the dataframe
df.columns = column_names

df.head()

Postal Code      Borough                           Neighbourhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

# 

## Getting latitude and longitude coordinates of each neighborhood

#### Importing libraries needed to find coordinates 

In [163]:
import pandas as pd
import io
import requests

In [164]:
pip install geopy 

Note: you may need to restart the kernel to use updated packages.


In [165]:
pip install folium

Note: you may need to restart the kernel to use updated packages.


### Adding coordinates to df

In [166]:
url="https://cocl.us/Geospatial_data"

s=requests.get(url).content
c=pd.read_csv(io.StringIO(s.decode('utf-8')))

df_toronto = df.join(c.set_index('Postal Code'), on='Postal Code')
df_toronto.head()

Postal Code      Borough                           Neighbourhood   Latitude  \
0         M1B  Scarborough                          Malvern, Rouge  43.806686   
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3         M1G  Scarborough                                  Woburn  43.770992   
4         M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

# 

## Finding venues in each neighborhood 

In [208]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)



In [175]:
toronto_venues = getNearbyVenues(names=df_toronto['Neighbourhood'],
                                   latitudes=df_toronto['Latitude'],
                                   longitudes=df_toronto['Longitude']
                                  )

Malvern, Rouge
Rouge Hill, Port Union, Highland Creek
Guildwood, Morningside, West Hill
Woburn
Cedarbrae
Scarborough Village
Kennedy Park, Ionview, East Birchmount Park
Golden Mile, Clairlea, Oakridge
Cliffside, Cliffcrest, Scarborough Village West
Birch Cliff, Cliffside West
Dorset Park, Wexford Heights, Scarborough Town Centre
Wexford, Maryvale
Agincourt
Clarks Corners, Tam O'Shanter, Sullivan
Milliken, Agincourt North, Steeles East, L'Amoreaux East
Steeles West, L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview, Henry Farm, Oriole
Bayview Village
York Mills, Silver Hills
Willowdale, Newtonbrook
Willowdale, Willowdale East
York Mills West
Willowdale, Willowdale West
Parkwoods
Don Mills
Don Mills
Bathurst Manor, Wilson Heights, Downsview North
Northwood Park, York University
Downsview
Downsview
Downsview
Downsview
Victoria Village
Parkview Hill, Woodbine Gardens
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto, Broadview North (Old East York)
The Danforth West, 

In [176]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                  8   
Bathurst Manor, Wilson Heights, Downsview North                        23   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      23   
Berczy Park                                                            59   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre, South Ce...                     16   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  14   
Cedarbrae                                                               8   
Central Bay Street                                                     63   
Christie                                                               15   
Church and Wellesley                                                   80   
Clarks Corners, Tam O'Shanter, Sullivan                                14   
Cliffside, Cliffcrest, Scarborough Village West                         2   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             35   
Davisville North                                                        9   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        5   
Don Mills                                                              24   
Dorset Park, Wexford Heights, Scarborough Town ...                      8   
Downsview                                                              15   
Dufferin, Dovercourt Village                                           15   
East Toronto, Broadview North (Old East York)                           4   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                     10   
Fairview, Henry Farm, Oriole                                           67   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                        10   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
Hillcrest Village                                                       5   
Humber Summit                                                           2   
Humberlea, Emery                                                        2   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         20   
Kennedy Park, Ionview, East Birchmount Park                             6   
Kensington Market, Chinatown, Grange Park                              65   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       11   
Lawrence Park                                                           4   
Leaside                                                                31   
Little Portugal, Trinity                                               43   
Malvern, Rouge                                                          1   
Milliken, Agincourt North, Steeles East, L'Amor.

### Finding all venue categories 

In [186]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Airport  Airport Food Court  \
0            0                  0        0                   0   
1            0                  0        0                   0   
2            0                  0        0                   0   
3            0                  0        0                   0   
4            0                  0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0                 0                   0            0              0   
1                 0                   0            0              0   
2                 0                   0            0              0   
3                 0                   0            0              0   
4                 0                   0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    1               0   
2          0           0           0       0     1    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bike Rental / Bike Share  Bike Shop  \
0           0                   0                         0          0   
1           0                   0                         0          0   
2           0                   0                         0          0   
3           0                   0                         0          0   
4           0                   0                         0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1     

### Frequency of each venue in the neighborhood 

In [187]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.000000   
8   Business reply mail Processing Centre, South C...     0.062500   
9   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
10                                Caledonia-Fairbanks     0.000000   
11              Canada Post Gateway Processing Centre     0.000000   
12                                          Cedarbrae     0.000000   
13                                 Central Bay Street     0.015873   
14                                           Christie     0.000000   
15                               Church and Wellesley     0.025000   
16            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
18                     Commerce Court, Victoria Hotel     0.000000   
19                                         Davisville     0.000000   
20                                   Davisville North     0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
22                                          Don Mills     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                          Downsview     0.000000   
25                       Dufferin, Dovercourt Village     0.000000   
26      East Toronto, Broadview North (Old East York)     0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
28                       Fairview, Henry Farm, Oriole     0.000000   
29             First Canadian Place, Underground city     0.000000   
30    Forest Hill North & West, Forest Hill Road Park     0.000000   
31                           Garden District, Ryerson     0.000000   
32                                          Glencairn     0.000000   
33                    Golden Mile, Clairlea, Oakridge     0.000000   
34                  Guildwood, Morningside, West Hill     0.000000   
35  Harbourfront East, Union Station, Toronto Islands     0.000000   
36                      High Park, The Junction South     0.000000   
37                                  Hillcrest Village     0.000000   
38                                      Humber Summit     0.000000   
39                                   Humberlea, Emery     0.000000   
40                                 Humewood-Cedarvale     0.000000   
41                     India Bazaar, The Beaches West     0.000000   
42        Kennedy Park, Ionview, East Birchmount Park     0.000000   
43          Kensington Market, Chinatown, Grange Park     0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
45                   Lawrence Manor, Lawrence Heights     0.000000   
46                                      Lawrence Park     0.000000   
47                                            Leaside     0.000000   
48                           Little Portugal, Trinity     0.023256   
49                                     Malvern, Rouge     0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...     0.000000   
52                        Moore Park, Summerhill East     0.000000   
53       New Toronto, Mimico South, Humber Bay Shores     0.000000   
54           North Park, Maple Leaf Park, Upwood Park     0.000000   
55                  North Toronto West, Lawrence Park     0.055556   
56                Northwest, West Humber - Clairvil

### Showing which and how many venues are in each neighborhood 

In [188]:
toronto_onehot.groupby('Neighborhood').count()

Yoga Studio  \
Neighborhood                                                      
Agincourt                                                     4   
Alderwood, Long Branch                                        8   
Bathurst Manor, Wilson Heights, Downsview North              23   
Bayview Village                                               4   
Bedford Park, Lawrence Manor East                            23   
Berczy Park                                                  59   
Birch Cliff, Cliffside West                                   4   
Brockton, Parkdale Village, Exhibition Place                 22   
Business reply mail Processing Centre, South Ce...           16   
CN Tower, King and Spadina, Railway Lands, Harb...           16   
Caledonia-Fairbanks                                           4   
Canada Post Gateway Processing Centre                        14   
Cedarbrae                                                     8   
Central Bay Street                                           63   
Christie                                                     15   
Church and Wellesley                                         80   
Clarks Corners, Tam O'Shanter, Sullivan                      14   
Cliffside, Cliffcrest, Scarborough Village West               2   
Commerce Court, Victoria Hotel                              100   
Davisville                                                   35   
Davisville North                                              9   
Del Ray, Mount Dennis, Keelsdale and Silverthorn              5   
Don Mills                                                    24   
Dorset Park, Wexford Heights, Scarborough Town ...            8   
Downsview                                                    15   
Dufferin, Dovercourt Village                                 15   
East Toronto, Broadview North (Old East York)                 4   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...           10   
Fairview, Henry Farm, Oriole                                 67   
First Canadian Place, Underground city                      100   
Forest Hill North & West, Forest Hill Road Park               4   
Garden District, Ryerson                                    100   
Glencairn                                                     4   
Golden Mile, Clairlea, Oakridge                              10   
Guildwood, Morningside, West Hill                             8   
Harbourfront East, Union Station, Toronto Islands           100   
High Park, The Junction South                                24   
Hillcrest Village                                             5   
Humber Summit                                                 2   
Humberlea, Emery                                              2   
Humewood-Cedarvale                                            4   
India Bazaar, The Beaches West                               20   
Kennedy Park, Ionview, East Birchmount Park                   6   
Kensington Market, Chinatown, Grange Park                    65   
Kingsview Village, St. Phillips, Martin Grove G...            4   
Lawrence Manor, Lawrence Heights                             11   
Lawrence Park                                                 4   
Leaside                                                      31   
Little Portugal, Trinity                                     43   
Malvern, Rouge                                                1   
Milliken, Agincourt North, Steeles East, L'Amor...            3   
Mimico NW, The Queensway West, South of Bloor, ...           13   
Moore Park, Summerhill East                                   3   
New Toronto, Mimico South, Humber Bay Shores                 11   
North Park, Maple Leaf Park, Upwood Park                      4   
North Toronto West, Lawrence Park                            18   
Northwest, West Humber - Clairville                           4   
Northwood Park, York University                               7   
Old Mill South, King's Mill Park

### Finding top 10 venues in each neighborhood 

In [205]:
top_venues = 10

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(top_venues))
    print('\n')

----Agincourt----
                             venue  freq
0        Latin American Restaurant  0.25
1                     Skating Rink  0.25
2                           Lounge  0.25
3                   Breakfast Spot  0.25
4              Monument / Landmark  0.00
5  Molecular Gastronomy Restaurant  0.00
6       Modern European Restaurant  0.00
7                Mobile Phone Shop  0.00
8               Miscellaneous Shop  0.00
9                      Yoga Studio  0.00


----Alderwood, Long Branch----
                        venue  freq
0                 Pizza Place  0.25
1                    Pharmacy  0.12
2                         Gym  0.12
3                 Coffee Shop  0.12
4                         Pub  0.12
5              Sandwich Place  0.12
6          Athletics & Sports  0.12
7  Modern European Restaurant  0.00
8                       Motel  0.00
9         Moroccan Restaurant  0.00


----Bathurst Manor, Wilson Heights, Downsview North----
                       venue  freq
0        

In [190]:
def return_most_common_venues(row, top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:top_venues]

### Adding info to a table showing top 10 venues in each neighborhood 

In [207]:
top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], top_venues)

neighborhoods_venues_sorted.head(103)

Neighborhood   1st Most Common Venue  \
0                                           Agincourt                  Lounge   
1                              Alderwood, Long Branch             Pizza Place   
2     Bathurst Manor, Wilson Heights, Downsview North             Coffee Shop   
3                                     Bayview Village                    Café   
4                   Bedford Park, Lawrence Manor East          Sandwich Place   
5                                         Berczy Park             Coffee Shop   
6                         Birch Cliff, Cliffside West         College Stadium   
7        Brockton, Parkdale Village, Exhibition Place                    Café   
8   Business reply mail Processing Centre, South C...      Light Rail Station   
9   CN Tower, King and Spadina, Railway Lands, Har...          Airport Lounge   
10                                Caledonia-Fairbanks                    Park   
11              Canada Post Gateway Processing Centre             Coffee Shop   
12                                          Cedarbrae                    Bank   
13                                 Central Bay Street             Coffee Shop   
14                                           Christie           Grocery Store   
15                               Church and Wellesley             Coffee Shop   
16            Clarks Corners, Tam O'Shanter, Sullivan             Pizza Place   
17    Cliffside, Cliffcrest, Scarborough Village West                   Motel   
18                     Commerce Court, Victoria Hotel             Coffee Shop   
19                                         Davisville          Sandwich Place   
20                                   Davisville North             Pizza Place   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn             Coffee Shop   
22                                          Don Mills                     Gym   
23  Dorset Park, Wexford Heights, Scarborough Town...       Indian Restaurant   
24                                          Downsview           Grocery Store   
25                       Dufferin, Dovercourt Village                  Bakery   
26      East Toronto, Broadview North (Old East York)       Convenience Store   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...                    Park   
28                       Fairview, Henry Farm, Oriole          Clothing Store   
29             First Canadian Place, Underground city             Coffee Shop   
30    Forest Hill North & West, Forest Hill Road Park           Jewelry Store   
31                           Garden District, Ryerson          Clothing Store   
32                                          Glencairn                     Pub   
33                    Golden Mile, Clairlea, Oakridge                  Bakery   
34                  Guildwood, Morningside, West Hill            Intersection   
35  Harbourfront East, Union Station, Toronto Islands             Coffee Shop   
36                      High Park, The Junction South                    Café   
37                                  Hillcrest Village    Fast Food Restaurant   
38                                      Humber Summit             Pizza Place   
39                                   Humberlea, Emery  Furniture / Home Store   
40                                 Humewood-Cedarvale              Playground   
41                     India Bazaar, The Beaches West    Fast Food Restaurant   
42        Kennedy Park, Ionview, East Birchmount Park       Convenience Store   
43          Kensington Market, Chinatown, Grange Park                    Café   
44  Kingsview Village, St. Phillips, Martin Grove ...          Sandwich Place   
45                   Lawrence Manor, Lawrence Heights          Clothing Store   
46                                      Lawrence Park                    Park   
47                                            Leaside             Coffee Shop   
48                           Little Portugal, Trinity                   